In [0]:
# Load the raw JSON data from the file you uploaded
raw_df = spark.read.json("/FileStore/tables/kafka_messages_purchase_trends.json")

# Display the first few rows to verify
display(raw_df)


payload schema List(List(128, 2022-07-19, 2021-07-30 22:55:09, 2022-08-13 13:18:13, 1645389887, 9, 3, 21, 7), null, c, List(postgresql, exampledb, 28063568, postgres, public, ["28063336","28063568"], false, purchase_trends, 1728270932892, 764, 2.4.2.Final, null), null, 1728270933149) List(List(List(before, List(List(null, date, io.debezium.time.Date, false, null, int32, 1), List(null, number_of_concert_tickets, null, true, null, int32, null), List(null, number_of_comedy_shows, null, true, null, int32, null), List(null, number_of_sport_events, null, true, null, int32, null), List(null, number_of_online_txns, null, true, null, int32, null), List(null, home_mortgage_purchased_ts, null, true, null, int64, null), List(null, customer_id, null, false, null, int32, null), List(null, datetime_created, io.debezium.time.MicroTimestamp, true, null, int64, 1), List(null, datetime_updated, io.debezium.time.MicroTimestamp, true, null, int64, 1)), postgres.public.purchase_trends.Value, true, struct, null), List(after, List(List(null, date, io.debezium.time.Date, false, null, int32, 1), List(null, number_of_concert_tickets, null, true, null, int32, null), List(null, number_of_comedy_shows, null, true, null, int32, null), List(null, number_of_sport_events, null, true, null, int32, null), List(null, number_of_online_txns, null, true, null, int32, null), List(null, home_mortgage_purchased_ts, null, true, null, int64, null), List(null, customer_id, null, false, null, int32, null), List(null, datetime_created, io.debezium.time.MicroTimestamp, true, null, int64, 1), List(null, datetime_updated, io.debezium.time.MicroTimestamp, true, null, int64, 1)), postgres.public.purchase_trends.Value, true, struct, null), List(source, List(List(null, version, null, false, null, string, null), List(null, connector, null, false, null, string, null), List(null, name, null, false, null, string, null), List(null, ts_ms, null, false, null, int64, null), List(false, snapshot, io.debezium.data.Enum, true, List(true,last,false,incremental), string, 1), List(null, db, null, false, null, string, null), List(null, sequence, null, true, null, string, null), List(null, schema, null, false, null, string, null), List(null, table, null, false, null, string, null), List(null, txId, null, true, null, int64, null), List(null, lsn, null, true, null, int64, null), List(null, xmin, null, true, null, int64, null)), io.debezium.connector.postgresql.Source, false, struct, null), List(op, null, null, false, string, null), List(ts_ms, null, null, true, int64, null), List(transaction, List(List(null, id, null, false, null, string, null), List(null, total_order, null, false, null, int64, null), List(null, data_collection_order, null, false, null, int64, null)), event.block, true, struct, 1)), postgres.public.purchase_trends.Envelope, false, struct, 1) List(List(255, 2020-07-14, 2022-04-04 04:27:29, 2022-05-29 07:56:13, 1660335757, 9, 1, 24, 1), null, c, List(postgresql, exampledb, 28063896, postgres, public, ["28063336","28063896"], false, purchase_trends, 1728270932892, 764, 2.4.2.Final, null), null, 1728270933150) List(List(List(before, List(List(null, date, io.debezium.time.Date, false, null, int32, 1), List(null, number_of_concert_tickets, null, true, null, int32, null), List(null, number_of_comedy_shows, null, true, null, int32, null), List(null, number_of_sport_events, null, true, null, int32, null), List(null, number_of_online_txns, null, true, null, int32, null), List(null, home_mortgage_purchased_ts, null, true, null, int64, null), List(null, customer_id, null, false, null, int32, null), List(null, datetime_created, io.debezium.time.MicroTimestamp, true, null, int64, 1), List(null, datetime_updated, io.debezium.time.MicroTimestamp, true, null, int64, 1)), postgres.public.purchase_trends.Value, true, struct, null), List(after, List(List(null, date, io.debezium.time.Date, false, null, int32, 1), List(null, number_of_concert_tickets, null, true, null, int32, null), List(null, number_of

In [0]:
# Save the raw data as Delta format in the bronze layer
raw_df.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/bronze/cdc_data")


In [0]:
spark.sql("""
CREATE TABLE IF NOT EXISTS bronze_cdc_data
USING DELTA
LOCATION '/mnt/bronze/cdc_data'
""")


Out[4]: DataFrame[]

In [0]:
from pyspark.sql import Window  # Import the Window function for window operations
from pyspark.sql.functions import col, row_number, sum, avg  # Import row_number and other necessary functions
from pyspark.sql.types import IntegerType 

bronze_df = spark.read.json("/FileStore/tables/kafka_messages_purchase_trends.json")

# Filter for insertions ('c') and updates ('u') based on the correct column path
insertions = bronze_df.filter(bronze_df["payload.op"] == 'c')
updates = bronze_df.filter(bronze_df["payload.op"] == 'u')

# Merge insertions and updates into one consolidated dataset
consolidated_data = insertions.union(updates)

# Flatten the nested structure and select the fields from payload.after
flattened_data = consolidated_data.select(
    "payload.after.customer_id",
    "payload.after.date",
    "payload.after.number_of_concert_tickets",
    "payload.after.number_of_comedy_shows",
    "payload.after.number_of_sport_events",
    "payload.after.number_of_online_txns",
    "payload.after.datetime_created",
    "payload.after.datetime_updated"
)

# Use a window function to keep the latest update for each customer_id based on datetime_updated
window_spec = Window.partitionBy("customer_id", "date").orderBy(col("datetime_updated").desc())

# Add a row number and filter to keep only the most recent row per customer_id
deduplicated_data = flattened_data.withColumn("row_num", row_number().over(window_spec)).filter(col("row_num") == 1).drop("row_num")

# Save the deduplicated, flattened data into the silver layer
deduplicated_data.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/silver/consolidated_data_flat_dedup")

# Create a Silver Delta Table for the deduplicated data
spark.sql("""
CREATE TABLE IF NOT EXISTS silver_consolidated_data_flat_dedup
USING DELTA
LOCATION '/mnt/silver/consolidated_data_flat_dedup'
""")

Out[9]: DataFrame[]

In [0]:
display(deduplicated_data)

customer_id date number_of_concert_tickets number_of_comedy_shows number_of_sport_events number_of_online_txns datetime_created datetime_updated 1 2021-09-22 5 5 0 28 2022-03-17 14:37:12 2022-08-13 22:40:50 2 2020-02-13 5 3 4 40 2020-02-16 07:07:52 2022-10-14 00:33:04 2 2022-09-13 3 3 5 37 2021-04-23 12:55:20 2021-02-01 20:15:57 2 2022-10-04 0 0 0 16 2020-10-01 18:30:25 2022-10-10 07:46:30 3 2020-07-08 4 5 10 39 2021-06-26 14:02:13 2021-10-11 03:16:07 3 2020-11-22 10 6 1 36 2021-11-12 03:49:45 2021-02-16 05:07:07 4 2020-12-10 1 10 6 35 2020-01-16 02:30:26 2020-02-23 23:58:48 4 2022-07-31 10 1 3 1 2020-02-16 20:43:10 2022-08-24 05:35:06 5 2020-09-07 1 5 2 9 2022-01-06 18:14:15 2020-06-15 09:24:30 5 2022-09-12 9 7 5 8 2022-11-29 19:54:57 2022-01-12 03:25:32 6 2020-04-26 9 6 8 27 2022-09-12 18:47:49 2021-07-13 21:26:23 6 2021-11-28 9 6 2 9 2022-01-15 02:14:12 2020-02-25 07:25:26 6 2022-03-04 9 3 5 44 2021-08-08 08:47:37 2022-10-26 22:49:28 6 2022-08-13 4 6 8 42 2022-01-24 07:32:00 2020-04-05 14:24:11 7 2020-10-08 5 8 5 41 2022-11-02 22:28:49 2022-05-24 16:55:32 9 2020-02-27 9 7 7 42 2022-07-29 18:45:39 2020-03-04 07:07:37 9 2022-09-09 3 4 10 6 2020-06-15 01:08:02 2021-04-03 01:25:00 10 2022-07-10 10 5 7 30 2021-10-20 04:25:08 2020-10-31 03:09:34 11 2020-11-27 9 7 2 29 2021-08-28 16:07:28 2022-11-20 07:12:34 11 2021-06-28 9 6 7 30 2020-02-14 05:57:29 2022-02-01 00:58:23 11 2022-10-05 6 3 5 12 2020-12-04 05:53:40 2022-11-04 10:12:12 12 2021-01-16 9 3 2 34 2020-07-25 13:26:36 2022-11-30 00:07:00 12 2022-01-29 5 5 7 7 2021-08-21 12:08:14 2020-05-24 13:34:48 12 2022-09-27 10 4 5 40 2020-02-03 13:29:12 2022-09-11 02:17:39 13 2020-09-09 3 5 6 2 2021-01-15 21:05:17 2020-04-05 04:33:47 13 2020-10-12 7 10 10 10 2021-04-14 21:04:44 2022-10-22 23:10:41 13 2021-04-08 5 3 0 48 2022-08-29 17:51:49 2022-08-18 10:44:51 13 2022-08-12 1 0 0 23 2020-02-27 06:59:03 2020-08-13 07:38:04 13 2022-10-29 2 10 2 17 2021-06-01 08:36:56 2020-09-24 16:56:13 14 2022-07-16 8 3 4 13 2020-01-31 19:39:18 2022-10-01 03:06:30 15 2022-05-29 5 4 4 28 2020-02-11 04:51:59 2021-07-18 22:35:40 15 2022-11-01 5 6 8 21 2021-05-22 21:40:52 2022-11-30 00:51:04 17 2021-10-27 1 0 3 14 2022-12-16 05:38:13 2021-04-20 04:16:47 19 2020-08-12 6 7 10 39 2020-01-29 12:51:51 2020-12-19 21:51:36 19 2021-09-24 8 8 2 49 2021-05-18 23:19:32 2022-10-22 17:01:37 19 2022-12-26 9 9 0 24 2022-04-11 20:05:07 2021-01-23 11:22:34 20 2021-02-07 9 6 3 12 2022-09-02 03:10:54 2021-04-18 01:02:16 21 2020-03-12 4 1 2 41 2021-12-23 02:29:16 2020-05-28 21:33:22 21 2021-08-09 5 9 8 22 2020-11-16 04:55:58 2021-11-30 12:25:33 21 2022-04-09 1 10 10 50 2021-09-07 02:59:48 2020-02-05 03:05:49 21 2022-12-27 5 10 7 30 2022-06-20 17:40:23 2020-09-15 08:30:58 22 2021-07-11 9 8 10 13 2021-02-02 17:47:03 2022-11-08 21:43:40 22 2021-12-24 5 7 4 41 2021-05-01 08:50:53 2022-10-04 14:46:07 23 2021-04-07 6 6 2 22 2021-02-24 10:05:00 2022-01-06 14:53:39 23 2021-10-12 9 3 0 41 2021-03-10 23:03:04 2020-07-05 03:04:33 23 2021-11-08 7 0 9 45 2021-02-22 01:08:36 2021-09-25 03:28:47 23 2021-12-24 2 2 10 47 2022-08-07 21:12:32 2021-05-17 18:43:17 23 2022-10-22 4 3 8 20 2022-01-02 01:21:27 2021-12-09 12:23:26 26 2022-01-03 3 4 5 38 2022-06-24 21:10:09 2020-10-26 08:25:08 27 2021-02-08 6 5 8 1 2020-02-07 17:01:52 2020-12-07 05:36:48 27 2021-03-22 1 4 2 6 2020-04-08 20:01:13 2021-07-20 19:30:49 27 2021-11-21 7 5 6 31 2020-08-14 16:19:13 2022-02-13 08:40:25 28 2022-01-18 2 3 4 26 2022-07-27 10:18:59 2022-03-04 15:10:49 28 2022-09-03 1 4 10 46 2020-02-27 01:33:41 2022-12-31 08:43:10 28 2022-10-14 2 3 9 44 2020-07-26 03:17:17 2020-04-16 15:49:12 29 2020-06-13 3 0 0 38 2020-11-25 10:34:10 2021-08-20 08:19:20 29 2022-11-29 1 8 10 33 2022-12-01 07:45:35 2021-01-01 01:47:07 30 2021-08-26 3 10 10 24 2022-06-03 05:34:25 2021-07-22 15:58:24 30 2022-04-24 7 4 5 45 2022-07-13 01:03:03 2021-01-03 05:17:40 30 2022-09-01 0 0 5 31 2021-04-22 15:05:12 2022-10-04 17:35:44 31 2021-01-31 7 1 5 37 2022-09-09 13:02:42 2020-09-06 02:11:34 31 2021-07-05 1 6 

In [0]:
silver_df = spark.read.format("delta").load("/mnt/silver/consolidated_data_flat_dedup")

# Ensure that the columns being aggregated are cast to IntegerType before the aggregation
aggregated_data = silver_df.groupBy("customer_id").agg(
    sum(col("number_of_online_txns").cast(IntegerType())).alias("total_online_txns"),
    avg(col("number_of_comedy_shows").cast(IntegerType())).alias("avg_comedy_shows")
)

# Save the aggregated data into the gold layer
aggregated_data.write.format("delta").mode("overwrite").save("/mnt/gold/customer_aggregates")

# Create a Gold Delta Table for customer aggregates
spark.sql("""
CREATE TABLE IF NOT EXISTS gold_customer_aggregates
USING DELTA
LOCATION '/mnt/gold/customer_aggregates'
""")

# Step 5: Query and Analyze the Gold Layer Data
# Query the gold layer to display the results
gold_df = spark.sql("SELECT * FROM gold_customer_aggregates")

# Show the results in the notebook
display(gold_df)

customer_id total_online_txns avg_comedy_shows 26 38 4.0 29 71 4.0 474 81 3.6666666666666665 65 38 4.0 191 156 5.8 418 67 6.5 222 36 4.333333333333333 270 31 6.5 293 58 5.5 243 86 5.333333333333333 278 108 3.2 367 77 5.666666666666667 442 26 6.5 19 112 8.0 54 52 6.0 296 22 6.0 287 43 2.0 348 84 3.5 415 46 1.0 112 14 5.0 155 22 3.0 167 36 6.0 299 10 4.0 385 75 5.666666666666667 237 130 5.2 241 87 1.6666666666666667 347 8 10.0 22 54 7.5 330 40 7.0 414 80 3.3333333333333335 130 9 9.0 196 118 6.75 427 8 4.0 486 97 8.0 487 56 1.5 7 41 8.0 77 56 4.5 34 47 9.0 184 78 5.333333333333333 463 21 1.0 188 23 6.5 126 31 6.0 202 51 5.0 228 24 5.0 274 22 3.0 262 81 6.0 325 65 6.0 406 40 1.0 50 24 4.0 149 40 7.0 421 95 6.0 264 88 4.0 229 111 7.333333333333333 110 36 8.0 190 95 2.6666666666666665 275 123 5.333333333333333 343 75 8.0 439 24 6.0 57 47 6.5 136 28 6.5 388 97 4.0 412 18 3.0 417 70 2.5 32 41 3.0 43 51 7.5 420 41 1.0 84 80 3.0 378 46 6.0 31 124 2.6666666666666665 376 70 5.5 119 94 1.0 395 98 2.6666666666666665 326 64 8.5 386 20 3.0 450 142 6.833333333333333 39 85 3.5 98 178 5.75 187 5 1.5 496 104 3.3333333333333335 201 100 6.333333333333333 232 26 10.0 402 23 8.0 203 13 5.666666666666667 116 70 2.0 145 46 2.0 488 33 3.5 157 44 7.0 124 4 3.0 181 1 6.0 363 52 8.0 227 42 3.0 369 63 1.0 455 125 5.75 71 51 6.666666666666667 143 43 10.0 370 17 6.0 161 2 6.0 193 53 7.0 365 101 4.25 443 90 4.5 6 122 5.25 68 36 7.333333333333333 342 41 5.5 466 110 4.75 72 26 4.0 87 82 7.0 58 25 0.5 255 80 5.666666666666667 258 14 7.0 320 45 7.5 107 41 10.0 221 25 0.0 266 46 8.5 271 100 4.5 424 43 6.0 9 48 5.5 316 42 7.0 407 54 1.5 27 38 4.666666666666667 63 21 6.0 158 120 5.6 389 22 1.0 397 51 6.5 51 130 4.0 56 77 5.333333333333333 178 145 4.333333333333333 353 25 1.0 234 75 2.5 239 92 3.3333333333333335 341 37 0.0 150 97 5.333333333333333 279 59 7.5 52 45 4.0 146 15 5.0 346 158 5.857142857142857 446 24 1.0 459 93 6.0 174 60 7.333333333333333 17 14 0.0 79 78 1.0 170 46 1.0 209 13 8.0 103 7 5.0 236 95 3.25 253 41 4.0 276 96 2.75 139 89 5.333333333333333 246 43 5.0 226 90 6.333333333333333 430 81 8.0 453 21 3.0 41 6 3.0 499 31 5.0 28 116 3.3333333333333335 33 88 6.5 88 51 2.5 248 42 5.25 257 44 6.0 384 60 1.5 405 77 4.6 138 104 7.0 207 31 3.5 498 19 2.0 235 115 5.666666666666667 304 108 3.25 307 6 7.0 462 33 7.5 114 68 3.6666666666666665 5 17 6.0 1 28 5.0 319 129 3.857142857142857 404 76 3.5 153 44 7.0 96 63 5.0 250 32 9.0 377 104 5.75 328 116 6.2 349 42 7.0 375 1 9.0 104 9 1.0 219 31 5.0 368 45 6.0 214 29 4.0 449 77 5.5 252 94 7.333333333333333 419 34 4.0 10 30 5.0 120 125 5.4 423 94 3.5 89 13 3.5 364 53 6.5 452 9 8.0 356 9 2.0 403 36 6.5 128 79 4.666666666666667 197 34 6.0 464 28 6.5 497 89 3.6666666666666665 85 26 7.333333333333333 106 30 7.5 332 70 5.5 301 45 4.333333333333333 411 68 6.0 177 66 3.0 448 43 2.5 48 26 2.5 67 40 9.5 224 6 0.0 142 103 7.75 168 42 4.0 324 46 1.0 481 61 6.5 100 28 6.0 247 51 6.0 467 81 8.0 131 16 3.5 318 44 2.0 294 1 2.0 451 128 5.0 108 18 6.0 218 74 8.5 333 55 4.0 339 30 0.0 44 32 2.0 132 41 7.5 309 43 4.0 392 123 5.6 471 118 4.666666666666667 123 70 10.0 127 37 5.0 345 42 4.0 210 68 7.0 205 4 10.0 225 33 3.0 323 17 1.0 352 102 4.333333333333333 220 59 7.0 249 22 5.5 383 17 4.0 61 84 3.5 303 6 8.0 379 81 5.0 192 31 8.5 213 109 4.5 337 31 6.0 440 97 4.0 454 9 1.0 473 94 5.333333333333333 156 25 4.5 429 50 1.0 160 18 5.0 283 10 10.0 3 75 5.5 435 52 6.5 206 135 7.5 382 2 1.0 478 15 4.5 482 48 8.0 101 105 4.5 292 74 6.0 431 87 3.0 83 33 4.0 362 34 6.0 491 43 5.0 12 81 4.0 200 123 6.333333333333333 295 64 6.0 355 70 6.0 141 30 1.0 55 0 3.0 373 44 2.5 280 79 7.5 322 21 6.0 390 37 5.5 492 64 7.5 62 4 9.0 182 83 4.0 186 114 7.75 331 68 5.666666666666667 11 71 5.333333333333333 49 79 7.333333333333333 290 49 8.5 437 3 4.0 35 61 6.0 371 96 6.25 166 40 5.5 260 33 1.0 80 107 4.75 321 106 8.0 380 17 1.5 199 30 6.333333333333333 477 25 2.0 2 93 2.0 269 91 4.0 465 55 6.5 66 70 3.0 154 85 7.0 265 74 7.5 162 20 0.0 244 26 5.0 344 86 6.0 428 117 4.

Top Customers by Event Participation

In [0]:
# Rank customers based on total event tickets purchased
top_customers = silver_df.groupBy("customer_id").agg(
    (sum("number_of_concert_tickets") + sum("number_of_comedy_shows") + sum("number_of_sport_events")).alias("total_event_tickets")
).orderBy(col("total_event_tickets").desc())

# Save the top customers analysis to Gold layer
top_customers.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/gold/top_customers_by_events")


In [0]:
display(top_customers)

customer_id total_event_tickets 300 124 450 108 346 106 154 102 178 101 147 101 319 97 405 89 237 84 392 84 391 80 186 79 326 78 193 78 278 77 191 76 6 75 292 75 51 74 436 74 397 73 196 72 328 72 21 72 158 71 206 71 272 71 23 71 495 70 120 68 371 68 426 68 259 68 440 67 321 67 64 67 98 66 236 66 295 65 276 64 80 64 13 64 312 64 138 63 252 63 142 63 416 63 36 62 425 62 33 61 377 61 101 61 269 61 137 61 275 60 370 60 19 59 184 58 248 58 379 58 213 58 199 58 68 56 172 56 330 55 486 55 455 55 304 55 75 55 87 54 226 54 368 54 352 54 11 54 49 54 289 54 262 53 203 53 423 53 67 53 451 53 46 53 271 52 464 52 117 52 444 52 474 51 367 51 139 51 235 51 134 51 285 51 222 50 385 50 107 50 174 50 430 50 12 50 99 50 239 49 301 49 475 49 70 49 47 49 365 48 220 48 192 48 263 48 488 47 466 47 411 47 331 47 194 47 42 47 201 46 387 46 40 46 169 46 265 45 230 45 97 45 60 45 311 45 266 44 27 44 56 44 85 44 30 44 22 43 264 43 229 43 297 43 396 43 188 42 71 42 443 42 52 42 249 42 465 42 344 42 428 42 175 42 442 41 241 41 214 41 317 41 72 40 9 40 384 40 403 40 247 40 200 40 243 39 343 39 150 39 128 39 481 39 123 39 473 39 360 39 216 39 472 39 57 38 255 38 320 38 424 38 170 38 28 38 498 38 364 38 106 38 290 38 357 38 148 38 388 37 496 37 329 37 173 37 129 37 484 37 462 36 108 36 210 36 3 36 280 36 163 36 456 36 418 35 136 35 131 35 478 35 92 35 284 35 211 35 43 34 279 34 349 34 218 34 66 34 159 34 363 33 100 33 471 33 160 33 308 33 408 33 394 33 167 32 325 32 190 32 376 32 386 32 132 32 362 32 313 32 15 32 151 32 121 32 414 31 146 31 459 31 332 31 4 31 358 31 77 30 202 30 84 30 31 30 116 30 497 30 435 30 355 30 122 30 5 29 404 29 448 29 309 29 156 29 302 29 476 29 152 29 273 29 143 28 333 28 303 28 373 28 166 28 338 28 395 27 452 27 177 27 467 27 205 27 492 27 182 27 76 27 281 27 270 26 54 26 96 26 250 26 89 26 383 26 431 26 231 26 293 25 187 25 127 25 61 25 390 25 245 25 126 24 417 24 119 24 342 24 63 24 283 24 401 24 130 23 421 23 439 23 39 23 197 23 2 23 310 23 217 23 29 22 287 22 420 22 402 22 157 22 181 22 253 22 88 22 10 22 380 22 477 22 233 22 348 21 378 21 227 21 114 21 219 21 449 21 48 21 238 21 234 20 207 20 153 20 162 20 493 20 204 20 427 19 34 19 44 19 482 19 35 19 314 19 335 19 133 19 336 19 7 18 407 18 209 18 453 18 62 18 102 18 20 18 483 18 406 17 149 17 232 17 58 17 258 17 103 17 141 17 55 17 118 17 374 17 161 16 339 16 337 16 491 16 164 16 176 16 422 16 180 16 469 16 487 15 228 15 274 15 369 15 316 15 341 15 41 15 257 15 307 15 104 15 324 15 14 15 291 15 109 15 398 15 458 15 32 14 79 14 499 14 437 14 433 14 350 14 409 14 296 13 83 13 125 13 494 13 86 13 26 12 65 12 112 12 299 12 110 12 353 12 419 12 356 12 224 12 345 12 298 12 59 12 393 12 315 12 438 12 256 12 457 12 489 12 340 12 347 11 225 11 322 11 282 11 53 11 389 10 1 10 195 10 82 10 445 10 91 10 221 9 375 9 318 9 454 9 429 9 244 9 140 9 286 9 415 8 145 8 124 8 446 8 382 8 189 8 93 8 261 8 50 7 412 7 246 7 294 7 323 7 223 6 168 5 260 5 155 4 463 4 17 4

Inactive Customers

In [0]:
from pyspark.sql.functions import col, current_date, datediff, max as spark_max

# Define the inactivity period (e.g., 180 days)
inactivity_threshold = 180

# Identify inactive customers based on their last purchase date
inactive_customers = (
    silver_df.groupBy("customer_id")
    .agg(
        spark_max(col("date")).alias("last_purchase_date")  # Use spark_max to avoid conflict with Python's max
    )
    .filter(datediff(current_date(), col("last_purchase_date")) > inactivity_threshold)
)

# Save the inactive customers to the Gold layer
inactive_customers.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/gold/inactive_customers")
display(inactive_customers)

customer_id last_purchase_date 1 2021-09-22 2 2022-10-04 3 2020-11-22 4 2022-07-31 5 2022-09-12 6 2022-08-13 7 2020-10-08 9 2022-09-09 10 2022-07-10 11 2022-10-05 12 2022-09-27 13 2022-10-29 14 2022-07-16 15 2022-11-01 17 2021-10-27 19 2022-12-26 20 2021-02-07 21 2022-12-27 22 2021-12-24 23 2022-10-22 26 2022-01-03 27 2021-11-21 28 2022-10-14 29 2022-11-29 30 2022-09-01 31 2021-10-09 32 2021-11-23 33 2022-11-12 34 2020-09-17 35 2020-09-01 36 2022-04-16 39 2022-08-05 40 2022-12-09 41 2020-01-21 42 2022-02-23 43 2022-05-25 44 2020-07-04 46 2021-04-28 47 2022-06-20 48 2022-02-07 49 2022-03-27 50 2020-05-21 51 2022-06-07 52 2022-06-30 53 2022-05-10 54 2022-07-09 55 2020-09-16 56 2021-05-30 57 2022-02-26 58 2021-05-09 59 2022-03-09 60 2022-11-05 61 2022-03-16 62 2020-09-28 63 2022-09-14 64 2022-07-30 65 2021-11-20 66 2022-09-22 67 2021-04-18 68 2021-12-22 70 2022-06-01 71 2022-07-24 72 2022-05-20 75 2022-06-20 76 2022-01-18 77 2021-08-27 79 2022-10-12 80 2022-09-12 82 2021-12-30 83 2022-05-19 84 2022-03-03 85 2022-10-25 86 2020-04-30 87 2022-06-07 88 2022-05-02 89 2021-10-20 91 2020-07-07 92 2022-12-25 93 2022-12-19 96 2022-03-30 97 2022-08-21 98 2022-09-23 99 2021-08-11 100 2021-05-19 101 2022-06-16 102 2021-01-26 103 2022-06-09 104 2020-07-26 106 2021-02-14 107 2022-07-08 108 2021-02-28 109 2022-08-07 110 2023-01-01 112 2021-03-17 114 2022-08-10 116 2022-10-31 117 2022-12-13 118 2022-11-13 119 2021-04-03 120 2022-12-12 121 2022-09-21 122 2022-11-01 123 2022-12-24 124 2020-05-25 125 2020-11-03 126 2021-05-02 127 2022-12-30 128 2022-07-19 129 2021-11-10 130 2020-06-02 131 2022-11-24 132 2022-04-10 133 2022-01-19 134 2022-09-16 136 2021-02-04 137 2022-06-16 138 2022-03-25 139 2022-10-07 140 2021-01-27 141 2022-09-09 142 2022-05-01 143 2022-03-17 145 2021-01-18 146 2020-12-23 147 2022-12-16 148 2021-05-02 149 2021-10-07 150 2022-04-27 151 2022-09-28 152 2022-12-24 153 2020-04-29 154 2021-09-12 155 2022-12-22 156 2021-07-31 157 2021-03-10 158 2022-06-13 159 2022-03-24 160 2022-10-25 161 2021-05-10 162 2020-05-01 163 2021-10-18 164 2022-05-14 166 2022-05-11 167 2022-10-28 168 2022-11-28 169 2022-11-26 170 2021-08-27 172 2021-06-04 173 2022-02-15 174 2022-08-25 175 2021-02-09 176 2022-11-27 177 2021-06-22 178 2022-08-09 180 2020-10-03 181 2022-01-30 182 2022-09-12 184 2021-07-24 186 2022-08-07 187 2021-05-02 188 2022-10-04 189 2022-08-25 190 2021-11-10 191 2022-06-01 192 2022-03-01 193 2021-10-16 194 2021-12-07 195 2022-01-07 196 2022-12-12 197 2021-08-01 199 2022-11-03 200 2021-05-05 201 2021-04-01 202 2021-10-03 203 2022-04-09 204 2022-11-12 205 2020-10-11 206 2021-06-03 207 2022-05-07 209 2020-02-10 210 2021-03-31 211 2022-05-20 213 2022-07-09 214 2021-06-14 216 2022-09-13 217 2020-11-12 218 2022-01-27 219 2021-06-19 220 2021-11-12 221 2022-04-20 222 2022-07-08 223 2020-07-13 224 2022-06-05 225 2022-09-20 226 2022-10-23 227 2021-11-09 228 2022-12-13 229 2022-11-22 230 2022-11-22 231 2020-05-18 232 2021-01-19 233 2021-02-03 234 2022-03-19 235 2021-07-01 236 2022-06-07 237 2022-06-18 238 2022-05-26 239 2022-02-27 241 2020-06-01 243 2022-07-26 244 2020-01-17 245 2021-12-21 246 2020-10-17 247 2021-04-22 248 2022-05-20 249 2022-06-18 250 2022-03-21 252 2022-10-03 253 2021-07-28 255 2022-06-27 256 2022-06-24 257 2020-07-10 258 2021-09-11 259 2022-11-12 260 2020-04-25 261 2020-08-05 262 2021-11-13 263 2021-10-20 264 2022-07-23 265 2022-11-06 266 2022-07-09 269 2022-04-14 270 2021-03-20 271 2022-12-28 272 2022-07-31 273 2022-05-09 274 2021-04-13 275 2020-12-25 276 2022-12-15 278 2022-02-23 279 2021-11-30 280 2021-01-16 281 2022-10-12 282 2020-04-20 283 2021-04-15 284 2020-04-03 285 2022-09-10 286 2020-11-27 287 2021-09-23 289 2022-08-09 290 2022-10-08 291 2021-08-28 292 2022-08-22 293 2022-07-29 294 2021-11-06 295 2022-12-16 296 2021-02-28 297 2022-05-05 298 2020-03-02 299 2020-11-03 300 2022-10-24 301 2022-03-12 302 2022-09-08 303 2020-07-14 304 2022-10-02 307 2021-08-18 308 2022-06-02 309 2021-08-12 310 2020-07-26 311 2021-08-18 312 2020-1

Event Type Preferences

In [0]:
from pyspark.sql.functions import greatest

# Create a Gold table for event type preferences
event_preference = silver_df.withColumn("preferred_event", greatest(
    col("number_of_concert_tickets"),
    col("number_of_comedy_shows"),
    col("number_of_sport_events")
)).select(
    "customer_id",
    "preferred_event"
)

# Save the event preference analysis to Gold layer
event_preference.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/gold/event_preference")
display(event_preference)

customer_id preferred_event 1 5 2 5 2 5 2 0 3 10 3 10 4 10 4 10 5 5 5 9 6 9 6 9 6 9 6 8 7 8 9 9 9 10 10 10 11 9 11 9 11 6 12 9 12 7 12 10 13 6 13 10 13 5 13 1 13 10 14 8 15 5 15 8 17 3 19 10 19 8 19 9 20 9 21 4 21 9 21 10 21 10 22 10 22 7 23 6 23 9 23 9 23 10 23 8 26 5 27 8 27 4 27 7 28 4 28 10 28 9 29 3 29 10 30 10 30 7 30 5 31 7 31 6 31 4 32 7 33 8 33 8 33 9 33 6 34 10 35 10 35 3 36 9 36 9 36 10 36 5 39 7 39 5 40 10 40 7 40 9 41 8 42 7 42 9 42 9 43 9 43 9 44 10 46 4 46 6 46 7 46 5 47 8 47 8 47 3 48 7 48 9 49 9 49 7 49 10 50 4 51 7 51 10 51 5 51 6 51 10 52 9 52 10 53 9 54 10 54 9 55 10 56 10 56 9 56 4 57 9 57 8 58 6 58 5 59 10 60 8 60 8 60 8 61 3 61 8 62 9 63 10 64 7 64 9 64 10 64 6 65 8 66 5 66 10 66 7 67 10 67 10 68 8 68 10 68 10 70 6 70 10 70 9 71 10 71 7 71 6 72 10 72 7 75 10 75 7 75 9 76 7 76 10 77 8 77 5 79 5 79 2 80 10 80 9 80 10 80 9 82 5 83 5 84 9 84 5 85 7 85 10 85 5 86 7 87 7 87 10 87 5 88 5 88 8 89 9 89 5 91 6 92 9 92 10 93 5 96 5 96 7 97 8 97 10 98 10 98 6 98 5 98 8 99 5 99 6 99 9 99 1 100 6 100 10 101 8 101 6 101 7 101 9 102 8 103 9 104 7 106 10 106 7 107 10 107 10 108 9 108 9 109 8 110 8 112 7 114 5 114 4 114 4 116 8 116 10 117 7 117 10 117 6 118 8 119 3 119 10 120 7 120 8 120 9 120 9 120 5 121 9 121 2 121 7 122 8 122 9 123 10 123 10 124 5 125 8 126 6 126 8 127 6 127 6 128 5 128 3 128 9 129 8 129 9 129 6 130 9 131 9 131 10 132 10 132 6 133 9 133 2 134 8 134 4 134 7 134 9 136 6 136 8 137 7 137 9 137 9 137 8 138 9 138 9 138 8 139 5 139 9 139 10 140 5 141 10 142 7 142 9 142 9 142 10 143 10 145 4 146 9 146 9 147 9 147 6 147 7 147 10 147 9 147 9 147 7 148 7 148 6 148 9 149 7 150 10 150 10 150 7 151 10 151 4 152 8 152 9 153 8 154 10 154 10 154 9 154 5 154 10 155 3 156 10 156 5 157 9 158 6 158 10 158 3 158 10 158 6 159 10 159 6 160 9 160 9 161 9 162 10 163 9 163 10 164 10 166 5 166 8 167 6 167 9 168 4 169 9 169 7 169 9 170 5 170 10 170 7 172 8 172 5 172 6 172 8 173 8 173 9 174 8 174 5 174 10 175 6 175 10 175 8 176 6 177 9 177 3 178 10 178 8 178 6 178 9 178 9 178 6 180 9 181 9 182 7 182 8 184 9 184 10 184 9 186 7 186 9 186 10 186 10 187 8 187 8 188 9 188 9 189 6 190 8 190 5 190 7 191 8 191 9 191 10 191 6 191 7 192 8 192 9 193 10 193 5 193 8 193 7 194 9 194 6 194 9 195 6 196 9 196 9 196 8 196 9 197 4 197 8 199 7 199 7 199 7 200 8 200 4 200 8 201 4 201 9 201 10 202 8 202 10 203 10 203 10 203 7 204 8 204 8 205 10 206 6 206 10 206 9 206 8 207 5 207 6 209 10 210 7 210 10 211 10 211 8 213 10 213 4 213 10 213 6 214 8 214 10 216 9 216 8 217 9 218 10 218 7 219 8 220 6 220 10 220 10 221 7 222 8 222 9 222 8 223 4 224 9 225 6 226 6 226 10 226 10 227 5 227 6 228 8 229 8 229 9 229 6 230 5 230 6 230 2 230 10 230 5 231 4 231 8 232 10 233 10 234 4 234 10 235 10 235 8 235 9 236 7 236 8 236 10 236 9 237 10 237 9 237 9 237 9 237 6 238 9 238 4 239 9 239 7 239 10 241 9 241 8 241 9 243 5 243 10 243 4 244 5 245 10 246 5 247 10 247 8 248 5 248 9 248 10 248 8 249 9 249 8 250 10 252 10 252 10 252 8 253 8 253 5 255 9 255 6 255 7 256 4 256 3 257 7 258 7 259 10 259 10 259 6 259 8 260 3 261 3 262 6 262 7 262 10 263 8 263 7 263 6 264 9 264 9 264 9 265 9 265 10 266 10 266 9 269 9 269 10 269 10 269 3 270 5 270 10 271 5 271 5 271 9 271 8 272 9 272 9 272 8 272 7 273 10 273 10 274 7 275 7 275 10 275 9 276 10 276 7 276 10 276 9 278 8 278 7 278 8 278 7 278 7 279 6 279 10 280 6 280 9 281 4 281 9 282 10 283 10 284 8 284 10 285 8 285 10 285 10 286 6 287 5 287 6 289 3 289 8 289 9 289 8 290 9 290 10 291 8 292 8 292 10 292 10 292 9 293 7 293 10 294 5 295 8 295 10 295 10 296 6 297 5 297 8 297 10 298 5 299 6 300 9 300 10 300 8 300 10 300 4 300 8 300 6 301 9 301 7 301 9 302 9 302 8 303 10 304 7 304 3 304 8 304 10 307 7 308 10 308 9 309 9 309 5 310 5 310 6 311 7 311 5 311 9 312 5 312 4 312 10 312 10 313 4 313 8 313 6 314 8 314 4 315 8 316 8 317 8 317 10 318 7 319 8 319 7 319 7 319 10 319 7 319 5 319 7 320 9 320 10 321 7 321 10 321 9 321 6 322 6 323 6 324 9 325 10 325 10 326 10 326 8 326 9 326 9 328 10 328 9 328 3 328 9 328 9 329 9 329 8 329 5 330 9 330 7 330 9 331 9 

Frequent Purchasers

In [0]:
# Define threshold for high engagement (e.g., more than 10 total events)
high_engagement_customers = silver_df.groupBy("customer_id").agg(
    (sum("number_of_concert_tickets") + sum("number_of_comedy_shows") + sum("number_of_sport_events")).alias("total_events")
).filter(col("total_events") > 10)

# Save the high engagement customers to Gold layer
high_engagement_customers.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("/mnt/gold/high_engagement_customers")
display(high_engagement_customers)

customer_id total_events 26 12 29 22 474 51 65 12 191 76 418 35 222 50 270 26 293 25 243 39 278 77 367 51 442 41 19 59 54 26 296 13 287 22 348 21 112 12 167 32 299 12 385 50 237 84 241 41 347 11 22 43 330 55 414 31 130 23 196 72 427 19 486 55 487 15 7 18 77 30 34 19 184 58 188 42 126 24 202 30 228 15 274 15 262 53 325 32 406 17 149 17 421 23 264 43 229 43 110 12 190 32 275 60 343 39 439 23 57 38 136 35 388 37 417 24 32 14 43 34 420 22 84 30 378 21 31 30 376 32 119 24 395 27 326 78 386 32 450 108 39 23 98 66 187 25 496 37 201 46 232 17 402 22 203 53 116 30 488 47 157 22 181 22 363 33 227 21 369 15 455 55 71 42 143 28 370 60 161 16 193 78 365 48 443 42 6 75 68 56 342 24 466 47 72 40 87 54 58 17 255 38 258 17 320 38 107 50 266 44 271 52 424 38 9 40 316 15 407 18 27 44 63 24 158 71 397 73 51 74 56 44 178 101 353 12 234 20 239 49 341 15 150 39 279 34 52 42 146 31 346 106 459 31 174 50 79 14 170 38 209 18 103 17 236 66 253 22 276 64 139 51 226 54 430 50 453 18 41 15 499 14 28 38 33 61 88 22 248 58 257 15 384 40 405 89 138 63 207 20 498 38 235 51 304 55 307 15 462 36 114 21 5 29 319 97 404 29 153 20 96 26 250 26 377 61 328 72 349 34 104 15 219 21 368 54 214 41 449 21 252 63 419 12 10 22 120 68 423 53 89 26 364 38 452 27 356 12 403 40 128 39 197 23 464 52 497 30 85 44 106 38 332 31 301 49 411 47 177 27 448 29 48 21 67 53 224 12 142 63 324 15 481 39 100 33 247 40 467 27 131 35 451 53 108 36 218 34 333 28 339 16 44 19 132 32 309 29 392 84 471 33 123 39 127 25 345 12 210 36 205 27 225 11 352 54 220 48 249 42 383 26 61 25 303 28 379 58 192 48 213 58 337 16 440 67 473 39 156 29 160 33 283 24 3 36 435 30 206 71 478 35 482 19 101 61 292 75 431 26 83 13 362 32 491 16 12 50 200 40 295 65 355 30 141 17 55 17 373 28 280 36 322 11 390 25 492 27 62 18 182 27 186 79 331 47 11 54 49 54 290 38 437 14 35 19 371 68 166 28 80 64 321 67 380 22 199 58 477 22 2 23 269 61 465 42 66 34 154 102 265 45 162 20 344 42 428 42 433 14 164 16 176 16 360 39 495 70 134 51 245 25 329 37 422 16 76 27 102 18 175 42 426 68 233 22 4 31 92 35 163 36 230 45 391 80 308 33 118 17 13 64 272 71 36 62 75 55 302 29 172 56 314 19 408 33 125 13 298 12 289 54 475 49 14 15 374 17 216 39 137 61 173 37 194 47 21 72 238 21 59 12 122 30 129 37 335 19 310 23 313 32 393 12 493 20 15 32 315 12 180 16 436 74 438 12 350 14 472 39 97 45 133 19 30 44 42 47 151 32 401 24 159 34 256 12 457 12 312 64 338 28 425 62 297 43 23 71 117 52 291 15 121 32 46 53 217 23 284 35 358 31 409 14 494 13 20 18 70 49 300 124 99 50 444 52 231 26 387 46 86 13 109 15 483 18 476 29 60 45 311 45 40 46 204 20 259 68 282 11 285 51 147 101 263 48 396 43 64 67 281 27 336 19 152 29 317 41 357 38 416 63 398 15 489 12 47 49 53 11 148 38 394 33 484 37 169 46 273 29 340 12 456 36 458 15 211 35 469 16